# Segmenting and Clustering Neighborhoods in Toronto

Downloading Dependencies

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print('Libraries imported.')

Libraries imported.


Importing BeautifulSoup

In [2]:
from bs4 import BeautifulSoup

Import get function from requests. Assigning the address of the web page to a variable named url.
Requesting the server the content of the web page by using get(), and storing the server’s response in the variable response.

In [3]:
from requests import get
url= "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
response = get(url)
print(response.text[:500])

<!DOCTYPE html>
<html class="client-nojs" lang="en" dir="ltr">
<head>
<meta charset="UTF-8"/>
<title>List of postal codes of Canada: M - Wikipedia</title>
<script>document.documentElement.className = document.documentElement.className.replace( /(^|\s)client-nojs(\s|$)/, "$1client-js$2" );</script>
<script>(window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_M","w


Reading table from wiki page using BeautifulSoup

In [4]:
html_wiki_page= BeautifulSoup(response.text, 'html.parser')
type(html_wiki_page)
page_tables = html_wiki_page.find_all('table')
Toronto_FSAs_table=page_tables[0]
Toronto_FSAs_table

<table class="wikitable sortable">
<tbody><tr>
<th>Postcode</th>
<th>Borough</th>
<th>Neighbourhood
</th></tr>
<tr>
<td>M1A</td>
<td>Not assigned</td>
<td>Not assigned
</td></tr>
<tr>
<td>M2A</td>
<td>Not assigned</td>
<td>Not assigned
</td></tr>
<tr>
<td>M3A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
</td></tr>
<tr>
<td>M4A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
</td></tr>
<tr>
<td>M5A</td>
<td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
<td><a href="/wiki/Harbourfront_(Toronto)" title="Harbourfront (Toronto)">Harbourfront</a>
</td></tr>
<tr>
<td>M5A</td>
<td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
<td><a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a>
</td></tr>
<tr>
<td>M6A</td>

Creating Dataframe
- The dataframe will consist of three columns: PostalCode, Borough, and Neighborhood
.

In [5]:
#del Toronto_FSAs_df

In [6]:

n_columns=0
n_rows=0
column_names=[]

for row in Toronto_FSAs_table.find_all('tr'):
    td_tags=row.find_all('td')
    if len(td_tags)>0:
        n_rows+=1
        if n_columns == 0:
            n_columns=len(td_tags)
    
    th_tags=row.find_all('th')
    if len(th_tags) > 0 and len(column_names) == 0:
        for th in th_tags:
            column_names.append(th.get_text().rstrip())
            


Toronto_FSAs_df= pd.DataFrame(columns=column_names,index=range(0,n_rows))



row_marker=-1

for row in Toronto_FSAs_table.find_all('tr'):
    column_marker=0
    columns=row.find_all('td')
    for column in columns:
        #print('row{},column{},text()'.format(row_marker,column_marker,column.get_text()))
        Toronto_FSAs_df.loc[row_marker, column_names[column_marker]] = column.get_text().rstrip()
        column_marker+=1
    row_marker+=1
    
Toronto_FSAs_df.head()  

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

- Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned

In [7]:
Toronto_FSAs_df=Toronto_FSAs_df[Toronto_FSAs_df.Borough != 'Not assigned']
Toronto_FSAs_df.reset_index()
Toronto_FSAs_df.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park.

In [8]:
Toronto_FSAs_df.loc[Toronto_FSAs_df['Neighbourhood']=='Not assigned', 'Neighbourhood']=Toronto_FSAs_df['Borough']
Toronto_FSAs_df.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

More than one neighborhood can exist in one postal code area. For example, in the table on the Wikipedia page, you will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma as shown in row 11 in the above table.

In [9]:
Toronto_FSAs_df_grouped=Toronto_FSAs_df.groupby(['Postcode','Borough'],as_index=False)['Neighbourhood'].apply(lambda x: "%s" % ', '.join(x)).to_frame(name='Neighbourhood').reset_index()

Toronto_FSAs_df_grouped.head()


Postcode      Borough                           Neighbourhood
0      M1B  Scarborough                          Rouge, Malvern
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2      M1E  Scarborough       Guildwood, Morningside, West Hill
3      M1G  Scarborough                                  Woburn
4      M1H  Scarborough                               Cedarbrae

If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park.

In the last cell of your notebook, use the .shape method to print the number of rows of your dataframe.

In [10]:
Toronto_FSAs_df_grouped.shape

(103, 3)

Now that you have built a dataframe of the postal code of each neighborhood along with the borough name and neighborhood name, in order to utilize the Foursquare location data, we need to get the latitude and the longitude coordinates of each neighborhood.

In [11]:
import geocoder

### Following is the code to get lat long from geocoder, but not able to get the geographical coordinates of the neighborhoods using the Geocoder package

for index, row in Toronto_FSAs_df_grouped.iterrows():
   
    postal_code=row['Postcode']
#initialize your variable to None
    lat_lng_coords = None

#loop until you get the coordinates

    while(lat_lng_coords is None):
        g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
        lat_lng_coords = g.latlng
#Assign Latitude and longitude
    row['Latitude']= lat_lng_coords[0]
    row['Longitude'] = lat_lng_coords[1]


Toronto_FSAs_df_grouped.head()

In [12]:
Geospatial_data=pd.read_csv("https://cocl.us/Geospatial_data")

In [13]:
Geospatial_data.columns=['Postcode', 'Latitude', 'Longitude']
Geospatial_data.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [14]:
Toronto_FSAs=pd.merge(Toronto_FSAs_df_grouped,Geospatial_data,on='Postcode')
Toronto_FSAs.head()

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

Generate maps to visualize your neighborhoods

In [15]:
import folium
latitude =Toronto_FSAs.Latitude.mean()
longitude =Toronto_FSAs.Longitude.mean()
venues_map = folium.Map(location=[latitude, longitude], zoom_start=10) # generate map centred around M1B


# add Ecco as a red circle mark
folium.features.CircleMarker(
    [latitude, longitude],
    radius=10,
    popup='Ecco',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(venues_map)


# add popular spots to the map as blue circle markers
for lat, lng, label in zip(Toronto_FSAs.Latitude, Toronto_FSAs.Longitude, Toronto_FSAs.Postcode):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        fill=True,
        color='blue',
        fill_color='blue',
        fill_opacity=0.6
        ).add_to(venues_map)

# display map
venues_map

## Explore a location

#### Define URL and client codes

In [16]:
CLIENT_ID="RFBWD0MXEMM3ESEHAPAJMAPGOA4GF5NBWA15BU1CYSRLLWSZ"
CLIENT_SECRET="M3LQZF1E0YG0EQJ0IUMDUFDQSGZN0RHNFXDH335O44CYPAIR"
VERSION='20180604'
radius=500
LIMIT=50



url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?client_id=RFBWD0MXEMM3ESEHAPAJMAPGOA4GF5NBWA15BU1CYSRLLWSZ&client_secret=M3LQZF1E0YG0EQJ0IUMDUFDQSGZN0RHNFXDH335O44CYPAIR&ll=43.70460773398059,-79.39715291165048&v=20180604&radius=500&limit=50'

#### Send get requests

In [17]:
results = requests.get(url).json()
#'There are {} around  restaurant.'.format(len(results['response']['groups'][0]['items']))

In [18]:
items=results['response']['groups'][0]['items']

In [19]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [20]:
venues = json_normalize(items) # flatten JSON
# filter columns
filtered_columns = ['venue.name', 'venue.categories'] + [col for col in venues.columns if col.startswith('venue.location.')] + ['venue.id']
venues_filtered = venues.loc[:, filtered_columns]

# filter the category for each row
venues_filtered['venue.categories'] = venues_filtered.apply(get_category_type, axis=1)

# clean columns
venues_filtered.columns = [col.split('.')[-1] for col in venues_filtered.columns]

venues_filtered.head(10)

name                     categories  \
0   Zezafoun Syrian Cousine                     Restaurant   
1  The Keg Steakhouse & Bar                     Steakhouse   
2                 Starbucks                    Coffee Shop   
3     Yonge Eglinton Square                          Plaza   
4          Five Doors North             Italian Restaurant   
5                   Loblaws                    Supermarket   
6                 Balsamico             Italian Restaurant   
7             Little Sister          Indonesian Restaurant   
8        Noorden Food x Bar                     Restaurant   
9                     Fresh  Vegetarian / Vegan Restaurant   

                             address  cc     city country       crossStreet  \
0                                NaN  CA  Toronto  Canada               NaN   
1                      2201 Yonge St  CA  Toronto  Canada   at Eglinton Ave   
2                  39 Eglinton Ave E  CA  Toronto  Canada          at Holly   
3                          Yonge St.  CA  Toronto  Canada  at Eglinton Ave.   
4                      2088 Yonge St  CA  Toronto  Canada               NaN   
5  101 Eglinton Ave E Toronto,Unit 1  CA  Toronto  Canada               NaN   
6                     2029 Yonge St.  CA  Toronto  Canada               NaN   
7                      2031 Yonge St  CA  Toronto  Canada        at Lola Rd   
8                     2110 Yonge St.  CA  Toronto  Canada               NaN   
9            90 Eglinton Avenue East  CA  Toronto  Canada  Yonge & Eglinton   

   distance                                   formattedAddress  \
0       216                       [Toronto ON M4S 2A4, Canada]   
1       121  [2201 Yonge St (at Eglinton Ave), Toronto ON M...   
2       260  [39 Eglinton Ave E (at Holly), Toronto ON M4P ...   
3       282  [Yonge St. (at Eglinton Ave.), Toronto ON M4S,...   
4       265                [2088 Yonge St, Toronto ON, Canada]   
5       360  [101 Eglinton Ave E Toronto,Unit 1, Toronto ON...   
6       345       [2029 Yonge St., Toronto ON M4S 2A2, Canada]   
7       340  [2031 Yonge St (at Lola Rd), Toronto ON M4S 2A...   
8       203               [2110 Yonge St., Toronto ON, Canada]   
9       325  [90 Eglinton Avenue East (Yonge & Eglinton), T...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 43.702667, 'lng':...  43.702667 -79.397120   
1  [{'label': 'display', 'lat': 43.70546405087482...  43.705464 -79.398085   
2  [{'label': 'display', 'lat': 43.70694, 'lng': ...  43.706940 -79.396908   
3  [{'label': 'display', 'lat': 43.70686372150796...  43.706864 -79.398751   
4  [{'label': 'display', 'lat': 43.70223554183669...  43.702236 -79.397526   
5  [{'label': 'display', 'lat': 43.70741230863768...  43.707412 -79.394909   
6  [{'label': 'display', 'lat': 43.70150469426698...  43.701505 -79.397162   
7  [{'label': 'display', 'lat': 43.70155150459908...  43.701552 -79.397163   
8  [{'label': 'display', 'lat': 43.70281430168457...  43.702814 -79.397645   
9  [{'label': 'display', 'lat': 43.70732441045359...  43.707324 -79.395649   

  postalCode state                        id  
0    M4S 2A4    ON  5abe3be1d3cce81e4407f9e5  
1    M4S 2B2    ON  4ad772faf964a520a70a21e3  
2    M4P 1A2    ON  4ad9c161f964a520a11a21e3  
3        M4S    ON  4c6c6c486af58cfae2ce8617  
4        NaN    ON  4b6b758ff964a520270a2ce3  
5    M4P 1H4    ON  5803b50738fa169524aca153  
6    M4S 2A2    ON  4ae86fb7f964a52053af21e3  
7    M4S 2A2    ON  53aca702498e3bbe34efc1bb  
8        NaN    ON  573e4cf6498e5c51f2319149  
9    M4P 1A6    ON  521e0c6c04939a8ad55d93d3

### Explore the neighborhood

In [56]:
def getNearbyVenues(names, latitudes, longitudes, radius=2000, LIMIT=30):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        print(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [57]:
#del Toronto_venues

Toronto_venues = getNearbyVenues(names=Toronto_FSAs['Neighbourhood'],
                                   latitudes=Toronto_FSAs['Latitude'],
                                   longitudes=Toronto_FSAs['Longitude']
                                  )

Rouge, Malvern
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4cd854fd3ec4b1f71900be3f', 'name': 'African Rainforest Pavilion', 'location': {'lat': 43.81772505914066, 'lng': -79.18343284457424, 'labeledLatLngs': [{'label': 'display', 'lat': 43.81772505914066, 'lng': -79.18343284457424}], 'distance': 1509, 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['Toronto ON', 'Canada']}, 'categories': [{'id': '58daa1558bbb0b01f18ec1fd', 'name': 'Zoo Exhibit', 'pluralName': 'Zoo Exhibits', 'shortName': 'Zoo Exhibit', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/zoo_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4cd854fd3ec4b1f71900be3f-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4bccf9bf511f9521ce0eb4c7', 'name': 'Fratelli Village Pizzeria', 'location': {'address': '384 Old Kingston Road', 'crossStreet': 'McMorrish Rd', 'lat': 43.784008053246104, 'lng': -79.16978707527669, 'labeledLatLngs': [{'label': 'display', 'lat': 43.784008053246104, 'lng': -79.16978707527669}], 'distance': 748, 'postalCode': 'M1C 1B6', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['384 Old Kingston Road (McMorrish Rd)', 'Toronto ON M1C 1B6', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d110941735', 'name': 'Italian Restaurant', 'pluralName': 'Italian Restaurants', 'shortName': 'Italian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/italian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4bccf9bf511f9521ce0eb4c7-0'}, {'reason

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4bc366dab492d13a51b2a860', 'name': 'Chick-N-Joy', 'location': {'address': '4449 Kingston Road', 'crossStreet': 'at Lawrence and Morningside', 'lat': 43.76875171771289, 'lng': -79.18798174616069, 'labeledLatLngs': [{'label': 'display', 'lat': 43.76875171771289, 'lng': -79.18798174616069}], 'distance': 579, 'postalCode': 'M1E 2N7', 'cc': 'CA', 'city': 'Scarborough', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['4449 Kingston Road (at Lawrence and Morningside)', 'Scarborough ON M1E 2N7', 'Canada']}, 'categories': [{'id': '4d4ae6fc7a7b7dea34424761', 'name': 'Fried Chicken Joint', 'pluralName': 'Fried Chicken Joints', 'shortName': 'Fried Chicken', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/friedchicken_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4bc366dab

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4bf470256a31d13a9ec7952e', 'name': 'The Real McCoy Burgers And Pizza', 'location': {'address': '1021 Markham Road', 'crossStreet': 'Brimorton', 'lat': 43.77408136872742, 'lng': -79.23049585681272, 'labeledLatLngs': [{'label': 'display', 'lat': 43.77408136872742, 'lng': -79.23049585681272}], 'distance': 1144, 'postalCode': 'M1K 2Y5', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1021 Markham Road (Brimorton)', 'Toronto ON M1K 2Y5', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d16c941735', 'name': 'Burger Joint', 'pluralName': 'Burger Joints', 'shortName': 'Burgers', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/burger_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4bf470256a31d13a9ec7952e-0'}, {'reasons': {'count': 0, 'ite

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4d6008f829ef236a8832a059', 'name': 'CANBE Foods Inc', 'location': {'address': '1760 Ellesmere Rd.', 'lat': 43.77354633117736, 'lng': -79.24608237285928, 'labeledLatLngs': [{'label': 'display', 'lat': 43.77354633117736, 'lng': -79.24608237285928}], 'distance': 532, 'postalCode': 'M1H 2V5', 'cc': 'CA', 'city': 'Scarborough', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1760 Ellesmere Rd.', 'Scarborough ON M1H 2V5', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d10f941735', 'name': 'Indian Restaurant', 'pluralName': 'Indian Restaurants', 'shortName': 'Indian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/indian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4d6008f829ef236a8832a059-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '562af766498e1f9621e63af1', 'name': 'UP Express - Weston Station', 'location': {'address': '1865 Weston Rd', 'lat': 43.700256, 'lng': -79.51366, 'labeledLatLngs': [{'label': 'display', 'lat': 43.700256, 'lng': -79.51366}], 'distance': 822, 'postalCode': 'M9N 1V9', 'cc': 'CA', 'neighborhood': 'Weston', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1865 Weston Rd', 'Toronto ON M9N 1V9', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d129951735', 'name': 'Train Station', 'pluralName': 'Train Stations', 'shortName': 'Train Station', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/trainstation_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-562af766498e1f9621e63af1-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 't

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ade06a6f964a520796721e3', 'name': 'Weston Golf And Country Club', 'location': {'address': '50 St Phillips Rd', 'crossStreet': 'at Weston Rd', 'lat': 43.701685, 'lng': -79.533228, 'labeledLatLngs': [{'label': 'display', 'lat': 43.701685, 'lng': -79.533228}], 'distance': 602, 'postalCode': 'M9P 2N6', 'cc': 'CA', 'city': 'Etobicoke', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['50 St Phillips Rd (at Weston Rd)', 'Etobicoke ON M9P 2N6', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d1e6941735', 'name': 'Golf Course', 'pluralName': 'Golf Courses', 'shortName': 'Golf Course', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/golfcourse_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4ade06a6f964a520796721e3-0'}, {'reasons': {'count': 0, 'items': [{'sum

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b97d2fcf964a5200d1835e3', 'name': 'Gourmet Express', 'location': {'address': '1735 Kipling Ave.', 'crossStreet': 'at Dixon Rd.', 'lat': 43.69311138097989, 'lng': -79.55729392261416, 'labeledLatLngs': [{'label': 'display', 'lat': 43.69311138097989, 'lng': -79.55729392261416}], 'distance': 511, 'postalCode': 'M9R 2Y8', 'cc': 'CA', 'city': 'Toronto', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['1735 Kipling Ave. (at Dixon Rd.)', 'Toronto ON M9R 2Y8', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d145941735', 'name': 'Chinese Restaurant', 'pluralName': 'Chinese Restaurants', 'shortName': 'Chinese', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/asian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b97d2fcf964a5200d1835e3-0'}, {'reasons': {'count': 0, 'item

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4fdb75c0e4b0d1917d92b018', 'name': 'Wok of Asia', 'location': {'lat': 43.73415221096142, 'lng': -79.60577591204354, 'labeledLatLngs': [{'label': 'display', 'lat': 43.73415221096142, 'lng': -79.60577591204354}], 'distance': 1512, 'cc': 'CA', 'country': 'Canada', 'formattedAddress': ['Canada']}, 'categories': [{'id': '4bf58dd8d48988d145941735', 'name': 'Chinese Restaurant', 'pluralName': 'Chinese Restaurants', 'shortName': 'Chinese', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/asian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4fdb75c0e4b0d1917d92b018-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '55a6feb3498e5be6bd83f25f', 'name': 'Starbucks', 'location': {'

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ba50113f964a52018cf38e3', 'name': 'Fortinos', 'location': {'address': '330 Queens Plate Dr', 'crossStreet': 'at Hwy 27', 'lat': 43.72158172960189, 'lng': -79.59623295870307, 'labeledLatLngs': [{'label': 'display', 'lat': 43.72158172960189, 'lng': -79.59623295870307}], 'distance': 1660, 'postalCode': 'M9W 7J7', 'cc': 'CA', 'city': 'Etobicoke', 'state': 'ON', 'country': 'Canada', 'formattedAddress': ['330 Queens Plate Dr (at Hwy 27)', 'Etobicoke ON M9W 7J7', 'Canada']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4ba50113f964a52018cf38e3-0'}, {'reasons': {'count': 0, 'item

In [58]:
Toronto_venues.shape

(3063, 7)

In [59]:
Toronto_venues.to_csv(r"C:\Users\23165948\Documents\JupyterNotebooks\Coursera_Capstone\Toronto_venues.csv")

In [60]:
Toronto_venues[Toronto_venues['Venue Category']=="Restaurant"]

Neighborhood  \
284                         Birch Cliff, Cliffside West   
350                                   Maryvale, Wexford   
597                            Silver Hills, York Mills   
770                                     Don Mills North   
792                    Flemingdon Park, Don Mills South   
812                    Flemingdon Park, Don Mills South   
821     Bathurst Manor, Downsview North, Wilson Heights   
850                     Northwood Park, York University   
863                     Northwood Park, York University   
897                         CFB Toronto, Downsview East   
1128                                            Leaside   
1230                       The Danforth West, Riverdale   
1280                                    Studio District   
1396                                         Davisville   
1510                        Cabbagetown, St. James Town   
1543                               Church and Wellesley   
1558                               Church and Wellesley   
1569                          Harbourfront, Regent Park   
1613                           Ryerson, Garden District   
1626                                     St. James Town   
1644                                     St. James Town   
1676                                        Berczy Park   
1726                           Adelaide, King, Richmond   
1774           Design Exchange, Toronto Dominion Centre   
1804                     Commerce Court, Victoria Hotel   
1846                  Bedford Park, Lawrence Manor East   
1912                Forest Hill North, Forest Hill West   
1946                The Annex, North Midtown, Yorkville   
1954                     Harbord, University of Toronto   
1976                     Harbord, University of Toronto   
2060                    Stn A PO Boxes 25 The Esplanade   
2074             First Canadian Place, Underground city   
2119                   Lawrence Heights, Lawrence Manor   
2160                                          Glencairn   
2246                                           Christie   
2336       Brockton, Exhibition Place, Parkdale Village   
2416                      The Junction North, Runnymede   
2473                             Parkdale, Roncesvalles   
2488                             Parkdale, Roncesvalles   
2493                             Parkdale, Roncesvalles   
2576              Canada Post Gateway Processing Centre   
2639       Humber Bay Shores, Mimico South, New Toronto   
2656                             Alderwood, Long Branch   
2724  Humber Bay, King's Mill Park, Kingsway Park So...   
2742  Kingsway Park South West, Mimico NW, The Queen...   

      Neighborhood Latitude  Neighborhood Longitude  \
284               43.692657              -79.264848   
350               43.750072              -79.295849   
597               43.757490              -79.374714   
770               43.745906              -79.352188   
792               43.725900              -79.340923   
812               43.725900              -79.340923   
821               43.754328              -79.442259   
850               43.767980              -79.487262   
863               43.767980              -79.487262   
897               43.737473              -79.464763   
1128              43.709060              -79.363452   
1230              43.679557              -79.352188   
1280              43.659526              -79.340923   
1396              43.704324              -79.388790   
1510              43.667967              -79.367675   
1543              43.665860              -79.383160   
1558              43.665860              -79.383160   
1569              43.654260              -79.360636   
1613              43.657162              -79.378937   
1626              43.651494              -79.375418   
1644              43.651494              -79.375418   
1676              43.644771              -79.373306   
1726              43.650571              -79.384568   
1774    

In [61]:
Toronto_venues[['Neighborhood','Venue Category','Venue']].groupby(['Neighborhood','Venue Category']).count()

Venue
Neighborhood                                       Venue Category                      
Adelaide, King, Richmond                           American Restaurant                2
                                                   Bakery                             1
                                                   Brazilian Restaurant               1
                                                   Breakfast Spot                     1
                                                   Burger Joint                       1
                                                   Burrito Place                      1
                                                   Café                               2
                                                   Concert Hall                       2
                                                   Greek Restaurant                   1
                                                   Gym                                2
                                                   Gym / Fitness Center               1
                                                   Hotel                              1
                                                   Mediterranean Restaurant           1
                                                   Monument / Landmark                1
                                                   Neighborhood                       1
                                                   New American Restaurant            1
                                                   Pizza Place                        1
                                                   Plaza                              1
                                                   Restaurant                         1
                                                   Speakeasy                          1
                                                   Steakhouse                         1
                                                   Sushi Restaurant                   1
                                                   Thai Restaurant                    1
                                                   Theater                            3
Agincourt                                          Asian Restaurant                   1
                                                   Bakery                             1
                                                   Breakfast Spot                     2
                                                   Cantonese Restaurant               1
                                                   Caribbean Restaurant               2
                                                   Chinese Restaurant                 3
                                                   Coffee Shop                        2
                                                   Gym                                1
                                                   Gym / Fitness Center               2
                                                   Indian Restaurant                  3
                                                   Korean Restaurant                  1
                                                   Lounge                             1
                                                   Malay Restaurant                   1
                                                   Noodle House                       1
                                                   Seafood Restaurant                 1
                                                   Sporting Goods Shop                1
                                                   Sri Lankan Restaurant              1
                                                   Steakhouse                         1
                                                   Supermarket                        2
                                                   Sushi Restaurant                   1
                                  

In [62]:
len(Toronto_venues['Venue Category'].unique())

243

### Analyze each Neighborhood

In [63]:
del Toronto_onehot
# one hot encoding
Toronto_onehot = pd.get_dummies(Toronto_venues[['Venue Category']], prefix="", prefix_sep="")
#print(Toronto_onehot.head())
# add neighborhood column back to dataframe
Toronto_onehot['Neighborhood'] = Toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Toronto_onehot.columns[-1]] + list(Toronto_onehot.columns[:-1])
Toronto_onehot = Toronto_onehot[fixed_columns]

Toronto_onehot.head(30)

Zoo Exhibit  Afghan Restaurant  Airport  Airport Lounge  \
0             1                  0        0               0   
1             0                  0        0               0   
2             0                  0        0               0   
3             0                  0        0               0   
4             0                  0        0               0   
5             1                  0        0               0   
6             1                  0        0               0   
7             1                  0        0               0   
8             1                  0        0               0   
9             1                  0        0               0   
10            1                  0        0               0   
11            1                  0        0               0   
12            0                  0        0               0   
13            0                  0        0               0   
14            0                  0        0               0   
15            0                  0        0               0   
16            0                  0        0               0   
17            0                  0        0               0   
18            1                  0        0               0   
19            0                  0        0               0   
20            0                  0        0               0   
21            0                  0        0               0   
22            1                  0        0               0   
23            0                  0        0               0   
24            0                  0        0               0   
25            0                  0        0               0   
26            0                  0        0               0   
27            0                  0        0               0   
28            1                  0        0               0   
29            1                  0        0               0   

    American Restaurant  Aquarium  Art Gallery  Art Museum  \
0                     0         0            0           0   
1                     0         0            0           0   
2                     0         0            0           0   
3                     0         0            0           0   
4                     0         0            0           0   
5                     0         0            0           0   
6                     0         0            0           0   
7                     0         0            0           0   
8                     0         0            0           0   
9                     0         0            0           0   
10                    0         0            0           0   
11                    0         0            0           0   
12                    0         0            0           0   
13                    0         0            0           0   
14                    0         0            0           0   
15                    0         0            0           0   
16                    0         0            0           0   
17                    0         0            0           0   
18                    0         0            0           0   
19                    0         0            0           0   
20                    0         0            0           0   
21                    0         0            0           0   
22                    0         0            0           0   
23                    0         0            0           0   
24                    0         0            0           0   
25                    0         0            0           0   
26                    0         0            0           0   
27                    1         0            0           0   
28                    0         0            0           0   
29                    0         0            0           0   

    Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0 

In [64]:
Toronto_grouped = Toronto_onehot.groupby('Neighborhood').mean().reset_index()
Toronto_grouped

Neighborhood  Zoo Exhibit  \
0                             Adelaide, King, Richmond          0.0   
1                                            Agincourt          0.0   
2    Agincourt North, L'Amoreaux East, Milliken, St...          0.0   
3    Albion Gardens, Beaumond Heights, Humbergate, ...          0.0   
4                               Alderwood, Long Branch          0.0   
5      Bathurst Manor, Downsview North, Wilson Heights          0.0   
6                                      Bayview Village          0.0   
7                    Bedford Park, Lawrence Manor East          0.0   
8                                          Berczy Park          0.0   
9                          Birch Cliff, Cliffside West          0.0   
10   Bloordale Gardens, Eringate, Markland Wood, Ol...          0.0   
11        Brockton, Exhibition Place, Parkdale Village          0.0   
12   Business Reply Mail Processing Centre 969 Eastern          0.0   
13                         CFB Toronto, Downsview East          0.0   
14   CN Tower, Bathurst Quay, Island airport, Harbo...          0.0   
15                         Cabbagetown, St. James Town          0.0   
16                                 Caledonia-Fairbanks          0.0   
17               Canada Post Gateway Processing Centre          0.0   
18                                           Cedarbrae          0.0   
19                                  Central Bay Street          0.0   
20           Chinatown, Grange Park, Kensington Market          0.0   
21                                            Christie          0.0   
22                                Church and Wellesley          0.0   
23                     Clairlea, Golden Mile, Oakridge          0.0   
24             Clarks Corners, Sullivan, Tam O'Shanter          0.0   
25     Cliffcrest, Cliffside, Scarborough Village West          0.0   
26   Cloverdale, Islington, Martin Grove, Princess ...          0.0   
27                      Commerce Court, Victoria Hotel          0.0   
28                                          Davisville          0.0   
29                                    Davisville North          0.0   
30   Deer Park, Forest Hill SE, Rathnelly, South Hi...          0.0   
31      Del Ray, Keelesdale, Mount Dennis, Silverthorn          0.0   
32            Design Exchange, Toronto Dominion Centre          0.0   
33                                     Don Mills North          0.0   
34   Dorset Park, Scarborough Town Centre, Wexford ...          0.0   
35                        Dovercourt Village, Dufferin          0.0   
36                                   Downsview Central          0.0   
37                                 Downsview Northwest          0.0   
38                                      Downsview West          0.0   
39         East Birchmount Park, Ionview, Kennedy Park          0.0   
40                                        East Toronto          0.0   
41                                    Emery, Humberlea          0.0   
42                        Fairview, Henry Farm, Oriole          0.0   
43              First Canadian Place, Underground city          0.0   
44                    Flemingdon Park, Don Mills South          0.0   
45                 Forest Hill North, Forest Hill West          0.0   
46                                           Glencairn          0.0   
47                   Guildwood, Morningside, West Hill          0.0   
48                      Harbord, University of Toronto          0.0   
49   Harbourfront East, Toronto Islands, Union Station          0.0   
50                           Harbourfront, Regent Park          0.0   
51                       High Park, The Junction South          0.0   
52              Highland Creek, Rouge Hill, Port Union          0.0   
53                                   Hillcrest Village          0.0   
54        Humber Bay Shores, Mimico South, New Toronto          0.0   
55   Humber Bay, King's Mill Park, Kingsway Park So...          0.

In [65]:
Toronto_grouped.shape

(103, 243)

In [66]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [67]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Toronto_grouped['Neighborhood']

for ind in np.arange(Toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Adelaide, King, Richmond               Theater   
1                                          Agincourt    Chinese Restaurant   
2  Agincourt North, L'Amoreaux East, Milliken, St...    Chinese Restaurant   
3  Albion Gardens, Beaumond Heights, Humbergate, ...           Coffee Shop   
4                             Alderwood, Long Branch           Coffee Shop   

  2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  \
0   American Restaurant                   Café          Concert Hall   
1     Indian Restaurant            Coffee Shop  Gym / Fitness Center   
2       Bubble Tea Shop  Vietnamese Restaurant   Dumpling Restaurant   
3  Fast Food Restaurant      Indian Restaurant           Pizza Place   
4           Pizza Place           Burger Joint    Seafood Restaurant   

       5th Most Common Venue 6th Most Common Venue    7th Most Common Venue  \
0                        Gym                 Plaza  New American Restaurant   
1             Breakfast Spot  Caribbean Restaurant              Supermarket   
2               Noodle House          Dessert Shop              Pizza Place   
3              Grocery Store           Flea Market       Chinese Restaurant   
4  South American Restaurant         Shopping Mall               Steakhouse   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Restaurant   Monument / Landmark        Thai Restaurant  
1   Sporting Goods Shop            Steakhouse  Sri Lankan Restaurant  
2           Coffee Shop           Event Space   Caribbean Restaurant  
3   Fried Chicken Joint        Sandwich Place                   Bank  
4             Bookstore        Breakfast Spot          Burrito Place

## Cluster Neighborhoods

In [68]:
# set number of clusters
kclusters = 5

Toronto_grouped_clustering = Toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 0, 0, 3, 3, 3, 0, 0, 1, 3])

In [69]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Toronto_final = Toronto_FSAs

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
Toronto_final = Toronto_FSAs.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')

Toronto_final.head()

Postcode      Borough                           Neighbourhood   Latitude  \
0      M1B  Scarborough                          Rouge, Malvern  43.806686   
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2      M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3      M1G  Scarborough                                  Woburn  43.770992   
4      M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.194353               0           Zoo Exhibit  Fast Food Restaurant   
1 -79.160497               3           Coffee Shop           Pizza Place   
2 -79.188711               3           Pizza Place  Fast Food Restaurant   
3 -79.216917               3           Coffee Shop            Beer Store   
4 -79.239476               0     Indian Restaurant            Steakhouse   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Pizza Place           Coffee Shop                   Zoo   
1        Sandwich Place        Breakfast Spot                  Bank   
2                  Park           Coffee Shop   Filipino Restaurant   
3    Chinese Restaurant     Indian Restaurant    Athletics & Sports   
4    Chinese Restaurant        Clothing Store     Fish & Chips Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Cosmetics Shop          Liquor Store   Fried Chicken Joint   
1    Mexican Restaurant  Fast Food Restaurant          Burger Joint   
2            Beer Store             Juice Bar           Supermarket   
3           Music Store           Supermarket        Sandwich Place   
4           Music Store      Sushi Restaurant         Movie Theater   

  9th Most Common Venue 10th Most Common Venue  
0  Caribbean Restaurant     Athletics & Sports  
1              Pharmacy      Food & Drink Shop  
2      Storage Facility             Sports Bar  
3        Discount Store        Thai Restaurant  
4   Sporting Goods Shop   Caribbean Restaurant

In [72]:

latitude =Toronto_final.Latitude.mean()
longitude =Toronto_final.Longitude.mean()
venues_map = folium.Map(location=[latitude, longitude], zoom_start=10) # generate map centred around centroid

clusters=[0,1,2,3,4,5]
cluster_color=['red','blue','yellow','green','purple']
for n in clusters:
    Toronto_plot=Toronto_final[Toronto_final['Cluster Labels']==n]
# add popular spots to the map as blue circle markers
    for lat, lng, label in zip(Toronto_plot.Latitude, Toronto_plot.Longitude, Toronto_plot['Neighbourhood']):
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            fill=True,
            color=cluster_color[n],
            fill_color=cluster_color[n],
            fill_opacity=0.6
            ).add_to(venues_map)

# display map
venues_map